In [1]:
from tensorflow import keras
import numpy as np
import os
import matplotlib.pyplot as plt
import tensorflow as tf
import cv2 as cv
from sklearn.model_selection import train_test_split
import random
import os
import glob
from PIL import Image, ImageOps
import numpy as np
import shutil
from tensorflow.keras.preprocessing.image import ImageDataGenerator
from tensorflow.keras.applications import EfficientNetB3
from tensorflow.keras.layers import Dense, GlobalAveragePooling2D

In [5]:
base_dir = r"D:\PROJECT\1_MACHINE LEARNING\THESIS_ALL_CLASSIFIER_DATABARU_2\dataset"
subfolders = ["benign", "EarlyPreB", "PreB", "ProB"]
segment_dir = r"D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Segmented"


SPLIT TRAIN VAL TEST

In [8]:
split_dir = r"D:\PROJECT\2_COMPUTER VISION\Image Segmentation\SPLIT"
split_train_dir = r"D:\PROJECT\2_COMPUTER VISION\Image Segmentation\SPLIT\train"
split_val_dir = r"D:\PROJECT\2_COMPUTER VISION\Image Segmentation\SPLIT\val"

augment_train_dir = r"D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented Train"
augment_val_dir = r"D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented Val"

In [9]:
splits = ["train", "test", "val"]
for split in splits:
  for subfolder in subfolders:
    output_folder = os.path.join(split_dir, split, subfolder)
    os.makedirs(output_folder, exist_ok=True)
    for filename in os.listdir(output_folder):
        os.remove(os.path.join(output_folder, filename))
    print(f"Isi file dalam folder {output_folder} telah dihapus.")

Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\SPLIT\train\benign telah dihapus.
Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\SPLIT\train\EarlyPreB telah dihapus.
Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\SPLIT\train\PreB telah dihapus.
Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\SPLIT\train\ProB telah dihapus.
Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\SPLIT\test\benign telah dihapus.
Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\SPLIT\test\EarlyPreB telah dihapus.
Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\SPLIT\test\PreB telah dihapus.
Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\SPLIT\test\ProB telah dihapus.
Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\SPLIT\val\benign telah dihapus.
Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\SP

In [10]:
def split_dataset(base_dir, output_dir, split_ratios=(0.7, 0.2, 0.1)):
    train_dir = os.path.join(output_dir, 'train')
    val_dir = os.path.join(output_dir, 'val')
    test_dir = os.path.join(output_dir, 'test')

    for subfolder in subfolders:
        subfolder_dir = os.path.join(base_dir, subfolder)
        images = [os.path.join(subfolder_dir, img) for img in os.listdir(subfolder_dir) if img.lower().endswith(('.png', '.jpg', '.jpeg', '.bmp', '.gif'))]

        random.shuffle(images)

        total_images = len(images)
        train_count = int(total_images * split_ratios[0])
        val_count = int(total_images * split_ratios[1])

        train_images = images[:train_count]
        val_images = images[train_count:train_count + val_count]
        test_images = images[train_count + val_count:]

        for image in train_images:
            shutil.copy(image, os.path.join(train_dir, subfolder, os.path.basename(image)))
        for image in val_images:
            shutil.copy(image, os.path.join(val_dir, subfolder, os.path.basename(image)))
        for image in test_images:
            shutil.copy(image, os.path.join(test_dir, subfolder, os.path.basename(image)))

        print(f'Kategori {subfolder}: {train_count} gambar untuk train, {val_count} gambar untuk val, {total_images - train_count - val_count} gambar untuk test.')

split_dataset(segment_dir, split_dir)

Kategori benign: 358 gambar untuk train, 102 gambar untuk val, 52 gambar untuk test.
Kategori EarlyPreB: 685 gambar untuk train, 195 gambar untuk val, 99 gambar untuk test.
Kategori PreB: 668 gambar untuk train, 191 gambar untuk val, 96 gambar untuk test.
Kategori ProB: 557 gambar untuk train, 159 gambar untuk val, 80 gambar untuk test.


AUGMENT DATA TRAINING

In [11]:
# function rotate
def rotate_image(image, angle):
    return image.rotate(angle, expand=True)

In [12]:
def zoom_in_image(image, zoom_factor):
    width, height = image.size
    new_width = int(width / zoom_factor)
    new_height = int(height / zoom_factor)

    left = (width - new_width) / 2
    top = (height - new_height) / 2
    right = (width + new_width) / 2
    bottom = (height + new_height) / 2

    image = image.crop((left, top, right, bottom))
    return image.resize((width, height), Image.Resampling.LANCZOS)

In [13]:
def flip_image(image, direction):
    if direction == 'horizontal':
        return ImageOps.mirror(image)
    elif direction == 'vertical':
        return ImageOps.flip(image)

In [14]:
# bikin subfolder buat augmentation train, trus hapus data yg udah ada di dalemnya biar kosong (i think)

for subfolder in subfolders:
  output_folder = os.path.join(augment_train_dir, subfolder)
  os.makedirs(output_folder, exist_ok=True)
  for filename in os.listdir(output_folder):
    os.remove(os.path.join(output_folder, filename))
  print(f"Isi file dalam folder {output_folder} telah dihapus.")

Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented Train\benign telah dihapus.
Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented Train\EarlyPreB telah dihapus.
Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented Train\PreB telah dihapus.
Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented Train\ProB telah dihapus.


In [15]:
for subfolder in subfolders:
    subfolder_path = os.path.join(split_train_dir, subfolder)
    output_dir = os.path.join(augment_train_dir, subfolder)
    image_files = glob.glob(os.path.join(subfolder_path, "*"))

    for image_file in image_files:
        original_image = Image.open(image_file)
        rotated_images = [rotate_image(original_image, angle) for angle in [90, 180, 270]]
        flipped_images = [flip_image(original_image, direction) for direction in ['horizontal', 'vertical']]
        zoom_factors = [np.random.uniform(1.2, 2.5) for _ in range(3)]
        zoomed_images = [zoom_in_image(original_image, zoom) for zoom in zoom_factors]

        base_filename = os.path.splitext(os.path.basename(image_file))[0]

        output_paths = [os.path.join(output_dir, f"{base_filename}_rotated_{angle}.jpg") for angle in [90, 180, 270]]
        output_paths += [os.path.join(output_dir, f"{base_filename}_flipped_{direction}.jpg") for direction in ['horizontal', 'vertical']]
        output_paths += [os.path.join(output_dir, f"{base_filename}_zoomed_{i}.jpg") for i in range(1, 4)]

        augmented_images = rotated_images + flipped_images + zoomed_images

        for img, path in zip(augmented_images, output_paths):
            img.save(path)
            print(f"{path} tersimpan")

D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented Train\benign\Sap_013 (1)_rotated_90.jpg tersimpan
D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented Train\benign\Sap_013 (1)_rotated_180.jpg tersimpan
D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented Train\benign\Sap_013 (1)_rotated_270.jpg tersimpan
D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented Train\benign\Sap_013 (1)_flipped_horizontal.jpg tersimpan
D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented Train\benign\Sap_013 (1)_flipped_vertical.jpg tersimpan
D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented Train\benign\Sap_013 (1)_zoomed_1.jpg tersimpan
D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented Train\benign\Sap_013 (1)_zoomed_2.jpg tersimpan
D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented Train\benign\Sap_013 (1)_zoomed_3.jpg tersimpan
D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented Train\benign\Sap_013 (10)_rotated_90.jpg tersimpan
D:\PROJECT\2_COMP

In [16]:
# augment folder val nya

In [17]:
# bikin subfolder buat augmentation, trus hapus data yg udah ada di dalemnya biar kosong (i think)

for subfolder in subfolders:
  output_folder = os.path.join(augment_val_dir, subfolder)
  os.makedirs(output_folder, exist_ok=True)
  for filename in os.listdir(output_folder):
    os.remove(os.path.join(output_folder, filename))
  print(f"Isi file dalam folder {output_folder} telah dihapus.")

Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented Val\benign telah dihapus.
Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented Val\EarlyPreB telah dihapus.
Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented Val\PreB telah dihapus.
Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented Val\ProB telah dihapus.


In [18]:
for subfolder in subfolders:
    subfolder_path = os.path.join(split_val_dir, subfolder)
    output_dir = os.path.join(augment_val_dir, subfolder)
    image_files = glob.glob(os.path.join(subfolder_path, "*"))

    for image_file in image_files:
        original_image = Image.open(image_file)
        rotated_images = [rotate_image(original_image, angle) for angle in [90, 180, 270]]
        flipped_images = [flip_image(original_image, direction) for direction in ['horizontal', 'vertical']]
        zoom_factors = [np.random.uniform(1.2, 2.5) for _ in range(3)]
        zoomed_images = [zoom_in_image(original_image, zoom) for zoom in zoom_factors]

        base_filename = os.path.splitext(os.path.basename(image_file))[0]

        output_paths = [os.path.join(output_dir, f"{base_filename}_rotated_{angle}.jpg") for angle in [90, 180, 270]]
        output_paths += [os.path.join(output_dir, f"{base_filename}_flipped_{direction}.jpg") for direction in ['horizontal', 'vertical']]
        output_paths += [os.path.join(output_dir, f"{base_filename}_zoomed_{i}.jpg") for i in range(1, 4)]

        augmented_images = rotated_images + flipped_images + zoomed_images

        for img, path in zip(augmented_images, output_paths):
            img.save(path)
            print(f"{path} tersimpan")

D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented Val\benign\Sap_013 (27)_rotated_90.jpg tersimpan
D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented Val\benign\Sap_013 (27)_rotated_180.jpg tersimpan
D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented Val\benign\Sap_013 (27)_rotated_270.jpg tersimpan
D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented Val\benign\Sap_013 (27)_flipped_horizontal.jpg tersimpan
D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented Val\benign\Sap_013 (27)_flipped_vertical.jpg tersimpan
D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented Val\benign\Sap_013 (27)_zoomed_1.jpg tersimpan
D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented Val\benign\Sap_013 (27)_zoomed_2.jpg tersimpan
D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented Val\benign\Sap_013 (27)_zoomed_3.jpg tersimpan
D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented Val\benign\Sap_013 (30)_rotated_90.jpg tersimpan
D:\PROJECT\2_COMPUTER VISIO

GABUNGIN DATA ORIGINAL DAN DATA AUGMENTED (TRAIN)

In [28]:
import os
import shutil

# Define paths

gabungan_train_dir = r"D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Train Gabungan"

split_dir = r"D:\PROJECT\2_COMPUTER VISION\Image Segmentation\SPLIT"
split_train_dir = r"D:\PROJECT\2_COMPUTER VISION\Image Segmentation\SPLIT\train"
split_val_dir = r"D:\PROJECT\2_COMPUTER VISION\Image Segmentation\SPLIT\val"

augment_train_dir = r"D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented Train"
augment_val_dir = r"D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented Val"

In [29]:
# bikin subfolder buat augmentation, trus hapus data yg udah ada di dalemnya biar kosong (i think)

for subfolder in subfolders:
  output_folder = os.path.join(gabungan_train_dir, subfolder)
  os.makedirs(output_folder, exist_ok=True)
  for filename in os.listdir(output_folder):
    os.remove(os.path.join(output_folder, filename))
  print(f"Isi file dalam folder {output_folder} telah dihapus.")

Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Train Gabungan\benign telah dihapus.
Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Train Gabungan\EarlyPreB telah dihapus.
Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Train Gabungan\PreB telah dihapus.
Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Train Gabungan\ProB telah dihapus.


In [30]:
# copy data ori ke folder train

for subfolder in subfolders:
  input_folder = os.path.join(split_train_dir, subfolder)
  output_folder = os.path.join(gabungan_train_dir, subfolder)
  for img_file in os.listdir(input_folder):
    img_path = os.path.join(input_folder, img_file)
    output_path = os.path.join(output_folder, img_file)
    shutil.copy(img_path, output_path)
    print(f"File {output_path} telah dicopy.")

File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Train Gabungan\benign\Sap_013 (1).jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Train Gabungan\benign\Sap_013 (10).jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Train Gabungan\benign\Sap_013 (11).jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Train Gabungan\benign\Sap_013 (12).jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Train Gabungan\benign\Sap_013 (13).jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Train Gabungan\benign\Sap_013 (14).jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Train Gabungan\benign\Sap_013 (15).jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Train Gabungan\benign\Sap_013 (16).jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Train Gabungan\benign\Sap_013 (17).jpg telah dicopy.
Fi

In [31]:
# copy data augment ke folder train

for subfolder in subfolders:
  input_folder = os.path.join(augment_train_dir, subfolder)
  output_folder = os.path.join(gabungan_train_dir, subfolder)
  for img_file in os.listdir(input_folder):
    img_path = os.path.join(input_folder, img_file)
    output_path = os.path.join(output_folder, img_file)
    shutil.copy(img_path, output_path)
    print(f"File {output_path} telah dicopy.")

File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Train Gabungan\benign\Sap_013 (1)_flipped_horizontal.jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Train Gabungan\benign\Sap_013 (1)_flipped_vertical.jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Train Gabungan\benign\Sap_013 (1)_rotated_180.jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Train Gabungan\benign\Sap_013 (1)_rotated_270.jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Train Gabungan\benign\Sap_013 (1)_rotated_90.jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Train Gabungan\benign\Sap_013 (1)_zoomed_1.jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Train Gabungan\benign\Sap_013 (1)_zoomed_2.jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Train Gabungan\benign\Sap_013 (1)_zoomed_3.jpg telah dicopy.
File D:\PROJECT\2_COMP

GABUNGAN DATA AUGMENT DAN DATA ORIGINAL (VAL)

In [32]:
import os
import shutil

# Define paths

gabungan_val_dir = r"D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Val Gabungan"

split_dir = r"D:\PROJECT\2_COMPUTER VISION\Image Segmentation\SPLIT"
split_train_dir = r"D:\PROJECT\2_COMPUTER VISION\Image Segmentation\SPLIT\train"
split_val_dir = r"D:\PROJECT\2_COMPUTER VISION\Image Segmentation\SPLIT\val"

augment_train_dir = r"D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented Train"
augment_val_dir = r"D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Augmented Val"

In [33]:
# bikin subfolder buat augmentation, trus hapus data yg udah ada di dalemnya biar kosong (i think)

for subfolder in subfolders:
  output_folder = os.path.join(gabungan_val_dir, subfolder)
  os.makedirs(output_folder, exist_ok=True)
  for filename in os.listdir(output_folder):
    os.remove(os.path.join(output_folder, filename))
  print(f"Isi file dalam folder {output_folder} telah dihapus.")

Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Val Gabungan\benign telah dihapus.
Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Val Gabungan\EarlyPreB telah dihapus.
Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Val Gabungan\PreB telah dihapus.
Isi file dalam folder D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Val Gabungan\ProB telah dihapus.


In [34]:
# copy data ori ke folder val

for subfolder in subfolders:
  input_folder = os.path.join(split_val_dir, subfolder)
  output_folder = os.path.join(gabungan_val_dir, subfolder)
  for img_file in os.listdir(input_folder):
    img_path = os.path.join(input_folder, img_file)
    output_path = os.path.join(output_folder, img_file)
    shutil.copy(img_path, output_path)
    print(f"File {output_path} telah dicopy.")

File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Val Gabungan\benign\Sap_013 (27).jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Val Gabungan\benign\Sap_013 (30).jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Val Gabungan\benign\Sap_013 (31).jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Val Gabungan\benign\Sap_013 (33).jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Val Gabungan\benign\Sap_013 (34).jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Val Gabungan\benign\Sap_013 (36).jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Val Gabungan\benign\Sap_013 (43).jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Val Gabungan\benign\Sap_013 (8).jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Val Gabungan\benign\Sap_013 (9).jpg telah dicopy.
File D:\PROJECT\2_COM

In [35]:
# copy data augment ke folder val

for subfolder in subfolders:
  input_folder = os.path.join(augment_val_dir, subfolder)
  output_folder = os.path.join(gabungan_val_dir, subfolder)
  for img_file in os.listdir(input_folder):
    img_path = os.path.join(input_folder, img_file)
    output_path = os.path.join(output_folder, img_file)
    shutil.copy(img_path, output_path)
    print(f"File {output_path} telah dicopy.")

File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Val Gabungan\benign\Sap_013 (27)_flipped_horizontal.jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Val Gabungan\benign\Sap_013 (27)_flipped_vertical.jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Val Gabungan\benign\Sap_013 (27)_rotated_180.jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Val Gabungan\benign\Sap_013 (27)_rotated_270.jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Val Gabungan\benign\Sap_013 (27)_rotated_90.jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Val Gabungan\benign\Sap_013 (27)_zoomed_1.jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Val Gabungan\benign\Sap_013 (27)_zoomed_2.jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VISION\Image Segmentation\Data Val Gabungan\benign\Sap_013 (27)_zoomed_3.jpg telah dicopy.
File D:\PROJECT\2_COMPUTER VIS